# Auto Encoder Cloud Detector 

In [1]:
# In a Jupyter notebook or IPython environment, run this in the first cell
%load_ext autoreload
%autoreload 2

In [2]:
import sys
import os
sys.path.append(os.path.abspath('../src'))

In [3]:
from datasets import (
    Puerto_Rico_Building_Dataset, 
    Cloud_DrivenData_Dataset
)

/opt/conda/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
from pathlib import Path
DATA_DIR = Path.cwd().parent.resolve() / "data/Cloud_DrivenData/final/public"
TRAIN_FEATURES = DATA_DIR / "train_features"
TRAIN_LABELS = DATA_DIR / "train_labels"
TRAIN_META_FILE = DATA_DIR / "train_metadata.csv"
BANDS = ["B04", "B03", "B02"] #"B08"
assert TRAIN_FEATURES.exists()
assert TRAIN_META_FILE.exists()

import pandas as pd
train_meta = pd.read_csv(TRAIN_META_FILE)

def add_paths(df: pd.DataFrame, feature_dir: Path, label_dir: Path = None, bands: list = BANDS) -> pd.DataFrame:
    """
    Adds file paths for each band and label to the dataframe based on chip_id.
    
    Args:
        df (pd.DataFrame): DataFrame containing chip_id (e.g., image identifiers).
        feature_dir (Path): Directory where feature TIF images are stored.
        label_dir (Path, optional): Directory where label TIF images are stored. Defaults to None.
        bands (list): List of band names (e.g., ["B02", "B03", ...]). Defaults to BANDS.
        
    Returns:
        pd.DataFrame: Updated dataframe with new columns for each band path and label path.
    
    Adds the following columns to the dataframe:
        - "{band}_path" for each band image.
        - "label_path" for the label image, if `label_dir` is provided.
        - "has_{band}_path" boolean column indicating if the feature file exists.
        - "has_image_channels" boolean column indicating if all feature band files exist.
        - "has_label_path" boolean column indicating if the label file exists (if `label_dir` is provided).
        - "accessible" boolean column indicating if all image channels and label file exist.
    """
    # Ensure feature_dir and label_dir are Path objects
    feature_dir = Path(feature_dir)
    if label_dir is not None:
        label_dir = Path(label_dir)

    selected_columns = ["chip_id", "location", "datetime", 
                        "cloudpath"
                        ]
    
    # Initialize columns to track file existence for each band
    for band in bands:
        df[f"{band}_path"] = feature_dir / df["chip_id"] / f"{band}.tif"
        # Check if the band file exists and add a boolean column
        df[f"has_{band}_path"] = df[f"{band}_path"].apply(lambda x: x.exists())
        selected_columns.append(f"{band}_path")

    # Add "has_image_channels" to check if all bands exist
    df["has_image_channels"] = df[[f"has_{band}_path" for band in bands]].all(axis=1)
    # Add label path and check existence if label_dir is provided
    if label_dir is not None:
        df["label_path"] = label_dir / (df["chip_id"] + ".tif")   
        # Check if the label file exists and add a boolean column
        df["has_label_path"] = df["label_path"].apply(lambda x: x.exists())
        selected_columns.append("label_path")
    
    # Add "accessible" column to check if all bands and label file exist
    df["accessible"] = df["has_image_channels"] & df["has_label_path"]
    
    return df[df["accessible"] == True][selected_columns]

train_meta = add_paths(train_meta, TRAIN_FEATURES, TRAIN_LABELS)

#################
import random
random.seed(9)  # set a seed for reproducibility

# put 1/3 of chips into the validation set
chip_ids = train_meta.chip_id.unique().tolist()
val_chip_ids = random.sample(chip_ids, round(len(chip_ids) * 0.2))

val_mask = train_meta.chip_id.isin(val_chip_ids)
val = train_meta[val_mask].copy().reset_index(drop=True)
train = train_meta[~val_mask].copy().reset_index(drop=True)

val.shape, train.shape
#################
# separate features from labels
feature_cols = ["chip_id"] + [f"{band}_path" for band in BANDS]

train_x = train[feature_cols].copy()
train_y = train[["chip_id", "label_path"]].copy()

val_x = val[feature_cols].copy()
val_y = val[["chip_id", "label_path"]].copy()

### Define Data Augmentation 

In [5]:
from torch.utils.data import DataLoader
import albumentations as A
from albumentations.pytorch import ToTensorV2

training_transform = A.Compose(
    [
        A.Resize(512, 512),
        A.HorizontalFlip(p=0.5),  # Random horizontal flip with 50% probability
        A.VerticalFlip(p=0.5),    # Random vertical flip with 50% probability
        A.RandomRotate90(p=0.5),  # Random 90 degree rotation with 50% probability
        A.ShiftScaleRotate(
            shift_limit=0.1, scale_limit=0.1, rotate_limit=15, p=0.5, border_mode=0
        ),  # Random shift, scale, and rotation with fill at borders
        A.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.1, p=0.5),  # Adjust color properties
        A.RandomBrightnessContrast(brightness_limit=0.3, contrast_limit=0.3, p=0.5),  # Adjust brightness and contrast
        A.GaussianBlur(blur_limit=(3, 5), p=0.3),  # Apply a Gaussian blur
        A.GaussNoise(var_limit=(10, 50), p=0.3),  # Add Gaussian noise
        ToTensorV2(),  # Convert to PyTorch tensors
    ], is_check_shapes=True
)

val_transform = A.Compose(
    [
       A.Resize(512, 512),
       ToTensorV2(),
    ], is_check_shapes=True
)

### Load DataLoader 

In [6]:
cloud_train = Cloud_DrivenData_Dataset(
    x_paths=train_x, 
    y_paths=train_y,
    bands=BANDS,
    transform=val_transform
)
cloud_val = Cloud_DrivenData_Dataset(
    x_paths=val_x, 
    y_paths=val_y,
    bands=BANDS,
    transform=val_transform
)

### Define the AutoEncoder Training/Validation Procedure 

In [ ]:
import torch
from torch.utils.data import DataLoader
from torch.optim import Adam
import torch.nn  as nn
from torch.nn import MSELoss
from torch.utils.tensorboard import SummaryWriter
from tqdm import tqdm
from torch.amp import autocast, GradScaler

def train_autoencoder(
    model, 
    train_dataset, 
    val_dataset=None, 
    num_epochs=20, 
    batch_size=64, 
    learning_rate=1e-3, 
    log_dir="./logs", 
    model_dir="models",
    experiment_name="experiment",
    device='cuda' if torch.cuda.is_available() else 'cpu', 
    training_log_interval=10,  # Log metrics every 10 steps
    use_amp=True  # Enable mixed precision training
):
    """
    Train an autoencoder with TensorBoard logging and GPU optimizations.

    Args:
        model (nn.Module): The autoencoder model to train.
        train_dataset (Dataset): Dataset for training.
        val_dataset (Dataset, optional): Dataset for validation. Defaults to None.
        num_epochs (int, optional): Number of epochs. Defaults to 20.
        batch_size (int, optional): Batch size for DataLoader. Defaults to 64.
        learning_rate (float, optional): Learning rate for optimizer. Defaults to 1e-3.
        log_dir (str, optional): Directory to save TensorBoard logs. Defaults to './logs'.
        device (str, optional): Device to use ('cuda' or 'cpu'). Defaults to GPU if available.
        training_log_interval (int): Interval for logging training metrics.
        use_amp (bool): Enable mixed precision training to optimize performance on GPUs.

    Returns:
        None
    """
    # Create a directory for the experiment
    timestamp = datetime.now().strftime("%Y%m%d-%H%M%S")
    log_dir = os.path.join(log_dir, f"{experiment_name}_{timestamp}")
    print(f"Experiment logs are recoded at {log_dir}")

    # Ensure model directory exists
    os.makedirs(model_dir, exist_ok=True)
    os.makedirs(log_dir, exist_ok=True)

    model = model.to(device)
    criterion = MSELoss()  # Mean Squared Error for reconstruction
    optimizer = Adam(model.parameters(), lr=learning_rate)
    scaler = GradScaler(enabled=use_amp)  # Mixed precision scaler

    # Dataloaders
    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, pin_memory=True)
    val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False, pin_memory=True) if val_dataset else None

    writer = SummaryWriter(log_dir=log_dir)

    for epoch in range(num_epochs):
        model.train()
        train_loss = 0.0
        step = 0  # To track batch steps

        with tqdm(train_loader, desc=f"Epoch {epoch + 1}/{num_epochs}", unit="batch") as t:
            for batch in t:
                step += 1
                inputs = batch["image"].to(device, non_blocking=True)
                optimizer.zero_grad()
                if use_amp:
                    with autocast(device_type=device, dtype=torch.float16):  # Mixed precision context
                        outputs = model(inputs)
                        loss = criterion(outputs, inputs)
                        # Backward pass
                        scaler.scale(loss).backward()
                        scaler.unscale_(optimizer)
                        scaler.step(optimizer)
                        scaler.update()
                else:
                    outputs = model(inputs)
                    loss = criterion(outputs, inputs)
                    loss.backward()
                    optimizer.update()

                train_loss += loss.item()

                # Log metrics to TensorBoard at intervals
                if step % training_log_interval == 0:
                    writer.add_scalar("Loss/Train_Batch", loss.item(), epoch * len(train_loader) + step)

                t.set_postfix(loss=loss.item())  # Display batch loss

        # Average loss over all batches in the epoch
        train_loss /= len(train_loader)
        writer.add_scalar("Loss/Train_Epoch", train_loss, epoch)
        print(f"Epoch {epoch + 1}/{num_epochs}, Train Loss: {train_loss:.4f}")

        # Validation Loop
        if val_loader:
            model.eval()
            val_loss = 0.0
            with autocast(device_type=device, dtype=torch.float16):
                for batch in val_loader:
                    inputs = batch["image"].to(device, non_blocking=True)
                    with autocast(enabled=use_amp):
                        outputs = model(inputs)
                        loss = criterion(outputs, inputs)
                    val_loss += loss.item()

            val_loss /= len(val_loader)
            writer.add_scalar("Loss/Validation", val_loss, epoch)
            print(f"Epoch {epoch + 1}/{num_epochs}, Validation Loss: {val_loss:.4f}")

        # Log images every 5 epochs
        if epoch % 5 == 0 or epoch == num_epochs - 1:
            writer.add_images("Reconstruction/Inputs", inputs[:8], epoch)
            writer.add_images("Reconstruction/Outputs", outputs[:8], epoch)

    writer.close()
    print("Training complete. Logs saved to:", log_dir)



In [9]:
from models import AutoEncoder 
model = AutoEncoder(
    num_input_channel=3, 
    base_channel_size=64, 
    ).to("cuda")

In [ ]:
train_autoencoder(
    model, 
    cloud_train, 
    val_dataset=cloud_val, 
    num_epochs=20, 
    batch_size=64, 
    learning_rate=1e-3, 
    log_dir="./logs", 
    device='cuda' if torch.cuda.is_available() else 'cpu', 
    training_log_interval=10,
    use_amp=True)

### Use AutoEncoder trained on Cloud Dataset as Cloud Detection Model (Reconstruction loss)

In [ ]:
### Define a threshold 

import numpy as np

def find_threshold(model, data, batch_size, loss_fn, device, confidence_interval=0.95):
    """
    Find a reconstruction loss threshold based on the training data.

    Args:
        model (nn.Module): The autoencoder model.
        data (Dataset): The dataset to compute reconstruction loss.
        batch_size (int): Batch size for DataLoader.
        loss_fn (function): The loss function to compute reconstruction error.
        device (str): Device to run the model on ('cpu' or 'cuda').
        confidence_interval (float, optional): Confidence interval for threshold. Defaults to 0.95.

    Returns:
        threshold (float): The threshold value for reconstruction loss.
        mean_loss (float): The mean reconstruction loss.
        std_loss (float): The standard deviation of the reconstruction loss.
    """
    data_loader = DataLoader(data, batch_size=batch_size, shuffle=False, pin_memory=True)

    model.eval()  # Set the model to evaluation mode
    model.to(device)  # Move model to the desired device

    all_losses = []  # To store all the individual losses

    with torch.no_grad():
        with tqdm(data_loader, desc=f"Threshold Computation", unit="batch") as t:
            for batch in t:
                inputs = batch["image"].to(device)
                outputs = model(inputs)
                
                # Compute the reconstruction loss (MSE)
                loss = loss_fn(outputs, inputs)
                all_losses.append(loss.item())

                t.set_postfix(loss=loss.item())  # Display batch loss

    # Convert list of losses to a NumPy array for easy manipulation
    all_losses = np.array(all_losses)
    
    # Calculate mean and standard deviation of the reconstruction loss
    mean_loss = np.mean(all_losses)
    std_loss = np.std(all_losses)
    
    # Calculate the threshold based on the confidence interval
    # For a 95% confidence interval, use 1.96 as k (the z-score for 95% confidence)
    z_score = 1.96 if confidence_interval == 0.95 else 1.64  # 1.64 for 90% confidence
    threshold = mean_loss + z_score * std_loss

    return threshold, mean_loss, std_loss


In [17]:
threshold, mean_loss, std_loss = find_threshold(model=model, data=cloud_val, batch_size=64, loss_fn=MSELoss(), device="cuda", confidence_interval=0.95)

Threshold Computation: 100%|██████████| 37/37 [00:44<00:00,  1.20s/batch, loss=0.000766]


In [22]:
threshold

np.float64(0.0012977699135690434)

In [23]:
model.save("../models/AutoEncoder_Cloud_Detector_0.001297.pth")

<class 'models.Auto_Encoder.AutoEncoder'> Model saved to ../models/AutoEncoder_Cloud_Detector_0.001297.pth


In [41]:
import matplotlib.pyplot as plt

def _display_image_pair(original, reconstructed, is_cloudy, step, normalize ):
    """
    Helper function to display original and reconstructed images side by side.
    
    Args:
        original (Tensor): Original input image.
        reconstructed (Tensor): Reconstructed output from the autoencoder.
        is_cloudy (bool): Detection result.
        step (int): Image index in the dataset.
    """
    # Un-normalize and convert tensors to numpy
    if normalize:
        mean = torch.tensor([0.485, 0.456, 0.406]).view(1, 3, 1, 1).to(original.device)
        std = torch.tensor([0.229, 0.224, 0.225]).view(1, 3, 1, 1).to(original.device)

        original = original * std + mean
        reconstructed = reconstructed * std + mean

    original = torch.clamp(original[0], 0, 1).cpu().permute(1, 2, 0).numpy()  # HWC format
    reconstructed = torch.clamp(reconstructed[0], 0, 1).cpu().permute(1, 2, 0).numpy()  # HWC format

    # Plot
    fig, axes = plt.subplots(1, 2, figsize=(10, 5))
    axes[0].imshow(original)
    axes[0].set_title(f"Original Image {step}")
    axes[0].axis("off")
    
    axes[1].imshow(reconstructed)
    axes[1].set_title(f"Reconstructed Image {step}\nCloudy: {is_cloudy}")
    axes[1].axis("off")
    
    plt.tight_layout()
    plt.show()
    
def cloud_detector(auto_encoder, dataset, threshold=0.3, display=False, normalize=False, image_key="image"):
    """
    Detect clouds in images using an autoencoder.
    
    Args:
        auto_encoder (nn.Module): Pre-trained autoencoder model.
        dataset (Dataset): Dataset containing the images to evaluate.
        threshold (float): Reconstruction loss threshold for detecting clouds.
        display (bool): Whether to display images and detection results.
        
    Returns:
        List[bool]: A list where each element is True if clouds are detected in the image, otherwise False.
    """
    
    device = next(auto_encoder.parameters()).device  # Ensure device matches model
    dataloader = DataLoader(dataset, batch_size=1, pin_memory=True)
    criterion = MSELoss()
   
    auto_encoder.eval()
    cloud_predictions = []
    
    with torch.no_grad():
        for step, batch in enumerate(dataloader):
            images = batch[image_key].to(device)  # Assuming dataset has "image" key
            reconstructed_images = auto_encoder(images)
            
            # Compute reconstruction loss
            loss = criterion(reconstructed_images, images).item()
            
            # Classify based on the threshold
            is_cloudy = (loss < threshold)
            cloud_predictions.append(is_cloudy)
            
            if display and is_cloudy:
                print(f"Image {step+1}: Loss = {loss:.4f}, Cloudy = {is_cloudy}")
                _display_image_pair(images, reconstructed_images, is_cloudy, step+1, normalize)

    return cloud_predictions

In [45]:
data_puerto = Puerto_Rico_Building_Dataset(
    base_dir="../data/Puerto_Rico_dataset/tiff_tiles",
    pre_disaster_dir="Pre_Event_Grids_In_TIFF",
    post_disaster_dir="Post_Event_Grids_In_TIFF",
    mask_dir="Post_Event_Grids_In_TIFF_mask",
    transform=None,
    extension="tif"
    )

In [46]:
len(data_puerto)

4855

In [ ]:
cloud_predictions = cloud_detector(model, dataset=data_puerto, threshold=0.001297, display=True, normalize=False, image_key="post_image")

In [ ]:
from models import AutoEncoder 
from torch.nn import MSELoss
cloud_filter_params = {"model_class": AutoEncoder(num_input_channel=3,base_channel_size=64), 
                        "device": "cuda", 
                        "file_path": "../models/AutoEncoder_Cloud_Detector_0.001297.pth",
                        "threshold": 0.001297, 
                        "loss": MSELoss,
                        "batch_size": 32
                        }

In [16]:
data_puerto = Puerto_Rico_Building_Dataset(
    base_dir="../data/Puerto_Rico_dataset/tiff_tiles",
    pre_disaster_dir="Pre_Event_Grids_In_TIFF",
    post_disaster_dir="Post_Event_Grids_In_TIFF",
    mask_dir="Post_Event_Grids_In_TIFF_mask",
    transform=None,
    extension="tif",
    cloud_filter_params=cloud_filter_params,
    preprocessing_mode="offline",
    filtered_list_path=None
    )

/home/onyxia/work/damaged-building-detector/src/models/Auto_Encoder.py:147: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  self.load_state_dict(torch.load(file_path))


<class 'models.Auto_Encoder.AutoEncoder'> Model loaded from ../models/AutoEncoder_Cloud_Detector_0.001297.pth
A AutoEncoder model has been loaded from ../models/AutoEncoder_Cloud_Detector_0.001297.pth on cuda.
Applying offline filtering...


Offline Filtering: 100%|██████████| 152/152 [02:58<00:00,  1.18s/batch]


In [17]:
len(data_puerto)

3957

In [18]:
data_puerto.display_data(list_indices=list(range(1,10)))